In [1]:
import os

##### To Access the OpenAI Embedding Model and LLM - ChatGPT turbo 3.5 for this project, paid OpenAI key is required 

In [2]:
os.environ["OPENAI_API_KEY"] = ''

##### import nest_asyncio because Jupyter runs in an event loop behind the scene -- and lot of our module use asyncio

In [3]:
import nest_asyncio

In [4]:
nest_asyncio.apply()

###### IMplementing and Testing Model on Book 1 : Sorcerers_Stone only

In [5]:
import llama_index

##### Using SemanticSplitter to create nodes, so that model would make nodes based on the context understanding and split document at relevant context point

In [6]:
from llama_index.core.node_parser import (SemanticSplitterNodeParser)

In [7]:
from llama_index.llms.openai import OpenAI

In [8]:
import requests

In [8]:
from langchain.embeddings import OpenAIEmbeddings

In [10]:
from llama_index.embeddings.openai import OpenAIEmbedding

##### Defining Embedded Model and LLM for the RAG

In [11]:
llm = OpenAI(model="gpt-3.5-turbo-0125")
embedding_model = OpenAIEmbedding(model="text-embedding-ada-002")

In [13]:
from llama_index.core import SimpleDirectoryReader

##### loading the document

In [14]:
documents = SimpleDirectoryReader(input_files=["harrypotter-pages-1.pdf","harrypotter-pages-2-1-75.pdf"]).load_data()

###### Embedded Model splitting the document using SemanticSplitter and store the content in different nodes

In [15]:
semantic_parser = SemanticSplitterNodeParser(buffer_size=1,breakpoint_percentile_threshold=95,embed_model=embedding_model)

##### Nodes are different size chunks that consists of part of the document. Splitter will break the document into different smaller size chunks called nodes

In [16]:
nodes = semantic_parser.get_nodes_from_documents(documents)

In [113]:
nodes

[TextNode(id_='88f67c95-7661-4e6c-bbba-7f794af7f06b', embedding=None, metadata={'page_label': '1', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'application/pdf', 'file_size': 1501472, 'creation_date': '2024-10-22', 'last_modified_date': '2024-10-21'}, excluded_embed_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], excluded_llm_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], relationships={<NodeRelationship.SOURCE: '1'>: RelatedNodeInfo(node_id='2a6f72f2-dbf0-4d22-b959-4f43bb9901f4', node_type=<ObjectType.DOCUMENT: '4'>, metadata={'page_label': '1', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'application/pdf', 'file_siz

In [18]:
from llama_index.core import SummaryIndex, VectorStoreIndex

###### Creating Summary and Vector Indexes

In [19]:
summary_index = SummaryIndex(nodes)
vector_index = VectorStoreIndex(nodes)

###### Creating Summary and Vector Engines

In [20]:
summary_query_engine = summary_index.as_query_engine(
    response_mode="tree_summarize",
    use_async=True,
    return_raw_results=True,
    top_k=3
)

In [21]:
vector_query_engine = vector_index.as_query_engine(return_raw_results=True,top_k=3)

In [22]:
from llama_index.core.tools import QueryEngineTool

###### Creating Summary and Vector Tools

In [23]:
summary_tool = QueryEngineTool.from_defaults(
    query_engine=summary_query_engine,
    description=(
        "Useful for summarization questions related to [document]"
    )
)

In [24]:
vector_tool = QueryEngineTool.from_defaults(
    query_engine=vector_query_engine,
    description=(
        "Useful for retrieving specific context from the [document]."
    ),
)

In [25]:
from llama_index.core.query_engine.router_query_engine import RouterQueryEngine

In [26]:
from llama_index.core.selectors import LLMSingleSelector

###### Defining Router

In [27]:
query_engine = RouterQueryEngine(
    selector=LLMSingleSelector.from_defaults(),
    query_engine_tools=[
        summary_tool,
        vector_tool,
    ],
    verbose=True
)

###### Provding Query to the model

In [27]:
query_engine.query("What is the use of Sorcerer's Stone ?")
print(str(response))

Selecting query engine 1: The question is asking about the specific context of the Sorcerer's Stone within the document, which aligns with the purpose of retrieving specific context..
The Sorcerer's Stone is a legendary substance with astonishing powers that can transform any metal into pure gold and produce the Elixir of Life, which grants immortality. The mention of the Sorcerer's Stone and its abilities can be found on page 198.


In [24]:
response = query_engine.query("What is the use of Sorcerer's Stone ? Mention the relevant passage where it is mentioned")
print(str(response))

Selecting query engine 1: The question is asking for specific context from the document, which is the use of Sorcerer's Stone. This choice is more relevant as it focuses on retrieving specific context..
The Sorcerer's Stone is a legendary substance with astonishing powers. It has the ability to transform any metal into pure gold and also produces the Elixir of Life, which grants immortality to the drinker. This information is mentioned in the passage where Harry and Ron read about the Sorcerer's Stone from a book pushed towards them by Hermione.


In [25]:
response = query_engine.query("What is the use of Sorcerer's Stone ? Mention the page number where it is mentioned")
print(str(response))

Selecting query engine 1: The question is asking for a specific context from the document, which is the mention of the Sorcerer's Stone and the page number where it is mentioned..
The Sorcerer's Stone is a legendary substance with astonishing powers that can transform any metal into pure gold and produce the Elixir of Life, which grants immortality. The mention of the Sorcerer's Stone and its abilities can be found on page 198.


In [32]:
response = query_engine.query("What happened in the game of chess ? Who are the players playing ? What is the end result? How ?")
print(str(response))

Selecting query engine 0: The question is asking for a summary of what happened in the game of chess, including the players and the end result. This choice is more aligned with summarization questions related to a document..


C:\Users\Aditi\AppData\Roaming\Python\Python311\site-packages\pydantic\main.py:212: RuntimeWarning: coroutine 'run_async_tasks.<locals>._gather' was never awaited
  validated_self = self.__pydantic_validator__.validate_python(data, self_instance=self)
C:\Users\Aditi\AppData\Roaming\Python\Python311\site-packages\pydantic\main.py:212: RuntimeWarning: coroutine 'Dispatcher.span.<locals>.async_wrapper' was never awaited
  validated_self = self.__pydantic_validator__.validate_python(data, self_instance=self)


In the game of chess, Ron sacrificed himself by allowing his piece to be taken by the opposing queen to clear the way for Harry to checkmate the opposing king. The players involved were Harry, Ron, and Hermione, with Ron as a knight, Hermione as a castle, and Harry as a bishop. The end result was that Ron's sacrifice enabled Harry to checkmate the opposing king, ultimately leading to their victory in the game and allowing them to proceed to the next challenge in their quest.


In [34]:
response = query_engine.query("Who is Hermione's life partner ? How do you know about that ?")
print(str(response))

Selecting query engine 1: Useful for retrieving specific context from the document..
Ron is Hermione's life partner. This can be inferred from the context where it mentions Hermione playing chess with Ron and how he reacts when Harry sits down next to him.


In [28]:
response = query_engine.query("What does Harry see in the Mirror of Erised?")
print(str(response))

Selecting query engine 1: Useful for retrieving specific context from the document..
Harry sees his family standing around him in the Mirror of Erised.


###### Checking the nodes fetched during a particular response

In [29]:
response.source_nodes

[NodeWithScore(node=TextNode(id_='737f2cc3-8254-4045-b9e1-5c5155d469e8', embedding=None, metadata={'page_label': '192', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'application/pdf', 'file_size': 1501472, 'creation_date': '2024-10-22', 'last_modified_date': '2024-10-21'}, excluded_embed_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], excluded_llm_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], relationships={<NodeRelationship.SOURCE: '1'>: RelatedNodeInfo(node_id='1d180bbd-da33-435e-9e84-e44c36a2e161', node_type=<ObjectType.DOCUMENT: '4'>, metadata={'page_label': '192', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'appl

In [42]:
# Summary Response node
response.source_nodes

[NodeWithScore(node=TextNode(id_='85dfc2a1-b210-4f07-8344-84b39d51acd1', embedding=None, metadata={'page_label': '1', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'application/pdf', 'file_size': 1501472, 'creation_date': '2024-10-22', 'last_modified_date': '2024-10-21'}, excluded_embed_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], excluded_llm_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], relationships={<NodeRelationship.SOURCE: '1'>: RelatedNodeInfo(node_id='b602e7ec-cebb-4e7a-952c-0f22f81f9f6d', node_type=<ObjectType.DOCUMENT: '4'>, metadata={'page_label': '1', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'applicat

In [41]:
response = query_engine.query("what is the summary of the document ?")
print(str(response))

Selecting query engine 0: Useful for summarization questions related to the document.
The document provides a detailed account of Harry Potter's journey from living with his neglectful relatives to discovering he is a wizard and attending Hogwarts School of Witchcraft and Wizardry. It follows Harry as he navigates through various adventures, encounters magical creatures, makes new friends, faces challenges at school, and ultimately protects the Sorcerer's Stone with the help of his friends Ron and Hermione. The story culminates in Gryffindor House tying with Slytherin for the House Cup, with Dumbledore awarding last-minute points for courage and bravery, leading to a celebratory end to the school year.


In [60]:
response = query_engine.query("Why Professor Snape doesn’t like Harry?")
print(str(response))

Selecting query engine 1: This choice is more relevant as it focuses on retrieving specific context from the document, which would help in understanding the specific reasons why Professor Snape doesn't like Harry..
Professor Snape doesn't like Harry because he perceives Harry as a celebrity and seems to harbor a strong dislike towards him, as evident from his behavior during the Potions lesson where he refers to Harry as a "celebrity" in a sarcastic manner and demonstrates a cold and empty demeanor towards him.


In [61]:
response.source_nodes

[NodeWithScore(node=TextNode(id_='7d4f2765-102f-42a7-ba5e-16bddb320f21', embedding=None, metadata={'page_label': '174', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'application/pdf', 'file_size': 1501472, 'creation_date': '2024-10-22', 'last_modified_date': '2024-10-21'}, excluded_embed_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], excluded_llm_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], relationships={<NodeRelationship.SOURCE: '1'>: RelatedNodeInfo(node_id='f48bed35-ad89-4cbf-81d7-b035cb790605', node_type=<ObjectType.DOCUMENT: '4'>, metadata={'page_label': '174', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'appl

In [43]:
response = query_engine.query("Why doesn’t Professor Snape like Harry?")
print(str(response))

Selecting query engine 1: This choice is more relevant as it focuses on retrieving specific context from the document, which would likely provide information on why Professor Snape doesn't like Harry..
Professor Snape doesn't like Harry because he actually hates him.


In [44]:
response.source_nodes

[NodeWithScore(node=TextNode(id_='1a6773ef-3abd-47ac-925c-e867b5bc06fd', embedding=None, metadata={'page_label': '127', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'application/pdf', 'file_size': 1501472, 'creation_date': '2024-10-22', 'last_modified_date': '2024-10-21'}, excluded_embed_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], excluded_llm_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], relationships={<NodeRelationship.SOURCE: '1'>: RelatedNodeInfo(node_id='131d6a76-102f-4a06-afc1-2eea650387d4', node_type=<ObjectType.DOCUMENT: '4'>, metadata={'page_label': '127', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'appl

In [62]:
response = query_engine.query("What did Harry's father did for Snape?")
print(str(response))

Selecting query engine 1: This choice is more relevant as it focuses on retrieving specific context from the document, which would provide information on what Harry's father did for Snape..
Harry's father saved Snape's life.


In [63]:
response.source_nodes

[NodeWithScore(node=TextNode(id_='adc22e6e-6bbd-4445-af02-c218780810d2', embedding=None, metadata={'page_label': '66', 'file_name': 'harrypotter-pages-2-1-75.pdf', 'file_path': 'D:\\Downloads\\harrypotter-pages-2-1-75.pdf', 'file_type': 'application/pdf', 'file_size': 438348, 'creation_date': '2024-10-22', 'last_modified_date': '2024-10-22'}, excluded_embed_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], excluded_llm_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], relationships={<NodeRelationship.SOURCE: '1'>: RelatedNodeInfo(node_id='14921696-62e1-433a-bc68-d0780826ff23', node_type=<ObjectType.DOCUMENT: '4'>, metadata={'page_label': '66', 'file_name': 'harrypotter-pages-2-1-75.pdf', 'file_path': 'D:\\Downloads\\harrypotter-pages-2-1-75.pdf', 'file_type': 'application/pdf', 'file_size': 438348, 'creation_date': '2024-10-22', 'last_modified_date': '2024

In [45]:
response = query_engine.query("What will happen in the next part ?")
print(str(response))

Selecting query engine 1: The question is asking about a specific event or context that will occur next in the document, which aligns with the purpose of retrieving specific context from the document..
Whispers and stares will continue to follow Harry as he moves around the school, with people trying to catch a glimpse of him and his scar.


In [46]:
response.source_nodes

[NodeWithScore(node=TextNode(id_='c7ae295f-ec9b-4b96-aad7-af60d57865c4', embedding=None, metadata={'page_label': '182', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'application/pdf', 'file_size': 1501472, 'creation_date': '2024-10-22', 'last_modified_date': '2024-10-21'}, excluded_embed_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], excluded_llm_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], relationships={<NodeRelationship.SOURCE: '1'>: RelatedNodeInfo(node_id='9951532d-05da-4342-85a1-d55466568dc2', node_type=<ObjectType.DOCUMENT: '4'>, metadata={'page_label': '182', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'appl

In [58]:
response = query_engine.query("Where does Hogwarts situated ?")
print(str(response))

Selecting query engine 1: Useful for retrieving specific context from the document. In this case, the specific context of where Hogwarts is situated..
Hogwarts is situated in a large entrance hall with stone walls lit with flaming torches, a high ceiling, and a magnificent marble staircase leading to the upper floors.


In [59]:
response.source_nodes

[NodeWithScore(node=TextNode(id_='7fe17c83-44b0-4d12-9508-5ac55f9d7b41', embedding=None, metadata={'page_label': '110', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'application/pdf', 'file_size': 1501472, 'creation_date': '2024-10-22', 'last_modified_date': '2024-10-21'}, excluded_embed_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], excluded_llm_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], relationships={<NodeRelationship.SOURCE: '1'>: RelatedNodeInfo(node_id='37042a73-52c7-4bb0-8c23-5ca2372568b7', node_type=<ObjectType.DOCUMENT: '4'>, metadata={'page_label': '110', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'appl

In [47]:
response = query_engine.query("Is the document, a good suggest for audience ?")
print(str(response))

Selecting query engine 0: The document is useful for summarization questions, which can help determine if it is a good suggestion for the audience..
The document is a good suggestion for the audience, particularly for those interested in fantasy literature, magical worlds, and stories involving elements of mystery, adventure, magic, friendship, and courage.


In [48]:
response.source_nodes

[NodeWithScore(node=TextNode(id_='85dfc2a1-b210-4f07-8344-84b39d51acd1', embedding=None, metadata={'page_label': '1', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'application/pdf', 'file_size': 1501472, 'creation_date': '2024-10-22', 'last_modified_date': '2024-10-21'}, excluded_embed_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], excluded_llm_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], relationships={<NodeRelationship.SOURCE: '1'>: RelatedNodeInfo(node_id='b602e7ec-cebb-4e7a-952c-0f22f81f9f6d', node_type=<ObjectType.DOCUMENT: '4'>, metadata={'page_label': '1', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'applicat

In [49]:
response = query_engine.query("What happened in the game of chess ? Who are the players playing ? What is the end result? How ?")
print(str(response))

Selecting query engine 0: The question is asking for a summary of what happened in the game of chess, including the players and the end result. This choice is more aligned with summarization questions related to a document..
In the game of chess, Ron sacrificed himself by allowing his piece to be taken, which ultimately led to Harry checkmating the opposing king. The players involved were Harry, Ron, and Hermione, with Ron as a knight, Hermione as a castle, and Harry as a bishop. The end result was Harry's victory through a strategic move that involved sacrificing Ron's piece to clear the way for Harry to checkmate the opposing king, ultimately winning the game and allowing them to proceed to the next challenge.


In [50]:
response.source_nodes

[NodeWithScore(node=TextNode(id_='85dfc2a1-b210-4f07-8344-84b39d51acd1', embedding=None, metadata={'page_label': '1', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'application/pdf', 'file_size': 1501472, 'creation_date': '2024-10-22', 'last_modified_date': '2024-10-21'}, excluded_embed_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], excluded_llm_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], relationships={<NodeRelationship.SOURCE: '1'>: RelatedNodeInfo(node_id='b602e7ec-cebb-4e7a-952c-0f22f81f9f6d', node_type=<ObjectType.DOCUMENT: '4'>, metadata={'page_label': '1', 'file_name': 'harrypotter-pages-1.pdf', 'file_path': 'D:\\C_Drive_Desktop\\AI_2024\\AI_Course\\Capstone\\harrypotter-pages\\harrypotter-pages-1.pdf', 'file_type': 'applicat

######  Model Evaluation

In [30]:
from datasets import Dataset

In [31]:
questions = ["Where does Hogwards situated ?", 
             "In which year, the book is published?",
             "Why doesn’t Professor Snape like Harry?",
             "What happened in the game of chess ? Who are the players playing ? What is the end result? How ?",
             "Who is Hermione's life partner ? How do you know about that ?",
             "What will happen in the next part ?",
             "What does Harry see in the Mirror of Erised?",
            ]


In [32]:
ground_truths = [["The narrow path had opened suddenly onto the edge of a great black lake. Perched atop a high mountain on the other side, its windows sparkling in the starry sky, was a vast castle with many turrets and towers."],
                ["Text copyright © 1997 by J.K. Rowling."],
                ["Professor Snape couldn’t bear being in your father’s debt. . . . I do believe he worked so hard to protect you this year because he felt that would make him and your father even. Then he could go back to hating your father’s memory in peace. "],
                ["I think, said Ron, we’re going to have to be chessmen. Well, Harry, you take the place of that bishop, and Hermione, you go there instead of that castle.I’m going to be a knight, said Ron. Ron started to direct the black pieces. They moved silently wherever he sent them. Harry’s knees were trembling. What if they lost? ... I’ve got to be taken. NO! Harry and Hermione shouted. That’s chess! snapped Ron. You’ve got to make some sacrifices! I’ll make my move and she’ll take me—that leaves you free to checkmate the king, Harry! ... He stepped forward, and the white queen pounced. She struck Ron hard across the head with her stone arm, and he crashed to the floor—Hermione screamed but stayed on her square—the white queen dragged Ron to one side. He looked as if he’d been knocked out. Shaking, Harry moved three spaces to the left. The white king took off his crown and threw it at Harry’s feet. They had won. The chessmen parted and bowed, leaving the door ahead clear."],
                ["The document does not specify Hermione's life partner, nor does it provide context about how one would know who that partner is. Content not present in the document."],
                ["The document does not contain information about future events or what will happen in the next part. Content not present in the document."],
                ["He had seen not only himself in the mirror, but a whole crowd of people standing right behind him... Harry was looking at his family, for the first time in his life."]
                ]


In [42]:
answers = ["Diagon Alley",
                "The book is published in 2014.",
                "Professor Snape doesn't like Harry because he actually hates him.",
                "In the game of chess, Harry, Ron, and Hermione played a life-sized game to reach the Sorcerer's Stone. Ron was a knight, Hermione was a castle, and Harry was a bishop. The end result was that Ron sacrificed himself by allowing the opposing queen to take him, which ultimately led to Harry putting the opposing king in checkmate, winning the game. This strategic move allowed them to successfully advance to the next challenge in their quest.",
                "Ron is Hermione's life partner. This can be inferred from the context where it mentions Hermione playing chess with Ron and how Ron reacts when Harry sits down next to him.",
                "In the next part, Harry will continue to experience whispers and stares from people as he moves around the school, likely due to the scar on his face that is drawing attention.",
                "Harry sees his family standing around him in the Mirror of Erised."
          ]


In [34]:
contexts = [["They\tsay\the\tmet\tvampires\tin\tthe\tBlack\tForest\tand\tthere\twas\ta\tnasty\tbit\to\ttrouble\twith\ta\thag\tnever\tbeen\tthe\tsame\tsince\tScared\tof\tthe\tstudents\tscared\tof\this\town\tsubject\tnow\twheres\tme\tumbrella\tVampires\tHags\tHarrys\thead\twas\tswimming\tHagrid\tmeanwhile\twas\tcounting\tbricks\tin\tthe\twall\tabove\tthe\ttrash\tcan\tThree\tup\t\t\t\ttwo\tacross\t\t\t\the\tmuttered\tRight\tstand\tback\tHarry\tHe\ttapped\tthe\twall\tthree\ttimes\twith\tthe\tpoint\tof\this\tumbrella\tThe\tbrick\the\thad\ttouched\tquivered\tit\twriggled\tin\tthe\tmiddle\ta\tsmall\thole\tappeared\tit\tgrew\twider\tand\twider\ta\tsecond\tlater\tthey\twere\tfacing\tan\tarchway\tlarge\tenough\teven\tfor\tHagrid\tan\tarchway\tonto\ta\tcobbled\tstreet\tthat\ttwisted\tand\tturned\tout\tof\tsight\tWelcome\tsaid\tHagrid\tto\tDiagon\tAlley\tthat\tnight\tyou\twon\tNorbert\tWhat\tdid\tthe\tstranger\tyou\twere\tplaying\tcards\twith\tlook\tlike\tDunno\tsaid\tHagrid\tcasually\the\twouldnt\ttake\this\tcloak\toff\tHe\tsaw\tthe\tthree\tof\tthem\tlook\tstunned\tand\traised\this\teyebrows\tIts\tnot\tthat\tunusual\tyeh\tget\ta\tlot\to\tfunny\tfolk\tin\tthe\tHogs\tHead\tthats\tone\to\tthe\tpubs\tdown\tin\tthe\tvillage\tMighta\tbin\ta\tdragon\tdealer\tmightnt\the\tI\tnever\tsaw\this\tface\the\tkept\this\thood\tup\tHarry\tsank\tdown\tnext\tto\tthe\tbowl\tof\tpeas\tWhat\tdid\tyou\ttalk\tto\thim\tabout\tHagrid\tDid\tyou\tmention\tHogwarts\tat\tall\tMighta\tcome\tup\tsaid\tHagrid\tfrowning\tas\the\ttried\tto\tremember\tYeah"],
                ["All\trights\treserved.\tNo\tpart\tof\tthis\tpublication\tmay\tbe\treproduced\tin\twhole\tor\tin\tpart,\tor\tstored\tin\ta\nretrieval\tsystem,\tor\ttransmitted\tin\tany\tform\tor\tby\tany\tmeans,\telectronic,\tmechanical,\tphotocopying,\nrecording,\tor\totherwise,\twithout\twritten\tpermission\tof\tthe\tpublisher.\nISBN\t9781781106471\tWhat’s\tthe\nmatter"],
                ["Harry\tborrowed\tRon’s\tquill\tscribbled\tYes\tplease\tsee\tyou\tlater\ton\tthe\tback\nof\tthe\tnote\tand\tsent\tHedwig\toff\tagain.\nIt\twas\tlucky\tthat\tHarry\thad\ttea\twith\tHagrid\tto\tlook\tforward\tto\tbecause\tthe\nPotions\tlesson\tturned\tout\tto\tbe\tthe\tworst\tthing\tthat\thad\thappened\tto\thim\tso\nfar.\nAt\tthe\tstart-of-term\tbanquet\tHarry\thad\tgotten\tthe\tidea\tthat\tProfessor\tSnape\ndisliked\thim.\tBy\tthe\tend\tof\tthe\tfirst\tPotions\tlesson\the\tknew\the’d\tbeen\twrong.\nSnape\tdidn’t\tdislike\tHarry\t—\the\thated\thim.\nPotions\tlessons\ttook\tplace\tdown\tin\tone\tof\tthe\tdungeons.\tIt\twas\tcolder\there\nthan\tup\tin\tthe\tmain\tcastle\tand\twould\thave\tbeen\tquite\tcreepy\tenough\twithout\nthe\tpickled\tanimals\tfloating\tin\tglass\tjars\tall\taround\tthe\twalls.\nSnape\tlike\tFlitwick\tstarted\tthe\tclass\tby\ttaking\tthe\troll\tcall\tand\tlike\nFlitwick\the\tpaused\tat\tHarry’s\tname.\nAh\tyes\the\tsaid\tsoftly\tHarry\tPotter\tOur\tnew\t—\tcelebrity.\nDraco\tMalfoy\tand\this\tfriends\tCrabbe\tand\tGoyle\tsniggered\tbehind\ttheir\nhands.\tSnape\tfinished\tcalling\tthe\tnames\tand\tlooked\tup\tat\tthe\tclass\tHis\teyes\nwere\tblack\tlike\tHagrid’s\tbut\tthey\thad\tnone\tof\tHagrid’s\twarmth.\tThey\twere\ncold\tand\tempty\tand\tmade\tyou\tthink\tof\tdark\ttunnels.\nYou\tare\there\tto\tlearn\tthe\tsubtle\tscience\tand\texact\tart\tof\tpotion-making\nhe\tbegan.\tHe\tspoke\tin\tbarely\tmore\tthan\ta\twhisper\tbut\tthey\tcaught\tevery\nword\t—\tlike\tProfessor\tMcGonagall\tSnape\thad\tthe\tgift\tof\tkeeping\ta\tclass\nsilent\twithout\teffort\tAs\tthere\tis\tlittle\tfoolish\twand-waving\there\tmany\tof\nyou\twill\thardly\tbelieve\tthis\tis\tmagic\tI\tdon’t\texpect\tyou\twill\treally\tunderstand\nthe\tbeauty\tof\tthe\tsoftly\tsimmering\tcauldron\twith\tits\tshimmering\tfumes\tthe\ndelicate\tpower\tof\tliquids\tthat\tcreep\tthrough\thuman\tveins\tbewitching\tthe\nmind\tensnaring\tthe\tsenses\t\tHe\nwas\tbeing\tmade\ta\tcup\tof\tstrong\ttea\tback\tin\tHagrid’s\thut\twith\tRon\tand\nHermione.\nIt\twas\tSnape\tRon\twas\texplaining\tHermione\tand\tI\tsaw\thim\tHe\twas\ncursing\tyour\tbroomstick\tmuttering\the\twouldn’t\ttake\this\teyes\toff\tyou.\nRubbish\tsaid\tHagrid\twho\thadn’t\theard\ta\tword\tof\twhat\thad\tgone\ton\tnext\nto\thim\tin\tthe\tstands\tWhy\twould\tSnape\tdo\tsomethin’\tlike\tthat\nHarry\tRon\tand\tHermione\tlooked\tat\tone\tanother\twondering\twhat\tto\ttell\nhim.\tHarry\tdecided\ton\tthe\ttruth.\nI\tfound\tout\tsomething\tabout\thim\the\ttold\tHagrid\tHe\ttried\tto\tget\tpast\nthat\tthree-headed\tdog\ton\tHalloween\tIt\tbit\thim\tWe\tthink\the\twas\ttrying\tto\nsteal\twhatever\tit’s\tguarding.\nHagrid\tdropped\tthe\tteapot.\nHow\tdo\tyou\tknow\tabout\tFluffy\the\tsaid.\nFluffy\nYeah\t—\the’s\tmine\t—\tbought\thim\toff\ta\tGreek\tchappie\tI\tmet\tin\tthe\tpub\tlas’\nyear\t—\tI\tlent\thim\tto\tDumbledore\tto\tguard\tthe\t—\nYes\tsaid\tHarry\teagerly.\nNow\tdon’t\task\tme\tanymore\tsaid\tHagrid\tgruffly\tThat’s\ttop\tsecret\tthat\nis.\nBut\tSnape’s\ttrying\tto\tsteal\tit.\nRubbish\tsaid\tHagrid\tagain\tSnape’s\ta\tHogwarts\tteacher\the’d\tdo\tnothin’\tof\tthe\tsort.\nSo\twhy\tdid\the\tjust\ttry\tand\tkill\tHarry\tcried\tHermione.\nThe\tafternoon’s\tevents\tcertainly\tseemed\tto\thave\tchanged\ther\tmind\tabout\nSnape.\nI\tknow\ta\tjinx\twhen\tI\tsee\tone\tHagrid\tI’ve\tread\tall\tabout\tthem!\tYou’ve\tgot\nto\tkeep\teye\tcontact\tand\tSnape\twasn’t\tblinking\tat\tall\tI\tsaw\thim!"],
                ["after\tall\tbut\tas\tthey\tonly\thad\todd\tmoments\tbetween\tlessons\tit\twasnt\nsurprising\ttheyd\tfound\tnothing\tWhat\tthey\treally\tneeded\twas\ta\tnice\tlong\nsearch\twithout\tMadam\tPince\tbreathing\tdown\ttheir\tnecks\nFive\tminutes\tlater\tRon\tand\tHermione\tjoined\thim\tshaking\ttheir\theads\nThey\twent\toff\tto\tlunch\nYou\twill\tkeep\tlooking\twhile\tIm\taway\twont\tyou\tsaid\tHermione\tAnd\nsend\tme\tan\towl\tif\tyou\tfind\tanything\nAnd\tyou\tcould\task\tyour\tparents\tif\tthey\tknow\twho\tFlamel\tis\tsaid\tRon\nItd\tbe\tsafe\tto\task\tthem\nVery\tsafe\tas\ttheyre\tboth\tdentists\tsaid\tHermione\nOnce\tthe\tholidays\thad\tstarted\tRon\tand\tHarry\twere\thaving\ttoo\tgood\ta\ttime\tto\nthink\tmuch\tabout\tFlamel\tThey\thad\tthe\tdormitory\tto\tthemselves\tand\tthe\ncommon\troom\twas\tfar\temptier\tthan\tusual\tso\tthey\twere\table\tto\tget\tthe\tgood\narmchairs\tby\tthe\tfire\tThey\tsat\tby\tthe\thour\teating"],
                ["\t\nThe\trest\tof\tthe\tteam\thung\tback\tto\ttalk\tto\tone\tanother\tas\tusual\tat\tthe\tend\tof\npractice\tbut\tHarry\theaded\tstraight\tback\tto\tthe\tGryffindor\tcommon\troom\nwhere\the\tfound\tRon\tand\tHermione\tplaying\tchess\tChess\twas\tthe\tonly\tthing\nHermione\tever\tlost\tat\tsomething\tHarry\tand\tRon\tthought\twas\tvery\tgood\tfor\nher\nDont\ttalk\tto\tme\tfor\ta\tmoment\tsaid\tRon\twhen\tHarry\tsat\tdown\tnext\tto\nhim\tI\tneed\tto\tconcen\t—\tHe\tcaught\tsight\tof\tHarrys\tface\tWhats\tthe\nmatter\twith\tyou\tYou\tlook\tterrible\nSpeaking\tquietly\tso\tthat\tno\tone\telse\twould\thear\tHarry\ttold\tthe\tother\ttwo\nabout\tSnapes\tsudden\tsinister\tdesire\tto\tbe\ta\tQuidditch\treferee\nDont\tplay\tsaid\tHermione\tat\tonceChoose\tunless\tyou\twish\tto\tstay\there\tforevermore\nTo\thelp\tyou\tin\tyour\tchoice\twe\tgive\tyou\tthese\tclues\tfour\nFirst\thowever\tslyly\tthe\tpoison\ttries\tto\thide\nYou\twill\talways\tfind\tsome\ton\tnettle\twines\tleft\tside\nSecond\tdifferent\tare\tthose\twho\tstand\tat\teither\tend\nBut\tif\tyou\twould\tmove\tonward\tneither\tis\tyour\tfriend\nThird\tas\tyou\tsee\tclearly\tall\tare\tdifferent\tsize\nNeither\tdwarf\tnor\tgiant\tholds\tdeath\tin\ttheir\tinsides\nFourth\tthe\tsecond\tleft\tand\tthe\tsecond\ton\tthe\tright\nAre\ttwins\tonce\tyou\ttaste\tthem\tthough\tdifferent\tat\tfirst\tsight\nHermione\tlet\tout\ta\tgreat\tsigh\tand\tHarry\tamazed\tsaw\tthat\tshe\twas\tsmiling\nthe\tvery\tlast\tthing\the\tfelt\tlike\tdoing\n"],
                ["Whats\tthe\nmatter\tT\t\nCHAPTER\t\tEIGHT\nTHE\tPOTIONS\tMASTER\nhere\tlook\nWhere\nNext\tto\tthe\ttall\tkid\twith\tthe\tred\thair\nWearing\tthe\tglasses\nDid\tyou\tsee\this\tface\nDid\tyou\tsee\this\tscar\nWhispers\tfollowed\tHarry\tfrom\tthe\tmoment\the\tleft\this\tdormitory\tthe\tnext\nday\tPeople\tlining\tup\toutside\tclassrooms\tstood\ton\ttiptoe\tto\tget\ta\tlook\tat\thim\nor\tdoubled\tback\tto\tpass\thim\tin\tthe\tcorridors\tagain\tstaring\t"],
                ["\tI\tI\tdidnt\tsee\tyou\tsir\nStrange\thow\tnearsighted\tbeing\tinvisible\tcan\tmake\tyou\tsaid\tDumbledore\nand\tHarry\twas\trelieved\tto\tsee\tthat\the\twas\tsmiling\nSo\tsaid\tDumbledore\tslipping\toff\tthe\tdesk\tto\tsit\ton\tthe\tfloor\twith\tHarry\nyou\tlike\thundreds\tbefore\tyou\thave\tdiscovered\tthe\tdelights\tof\tthe\tMirror\tof\nErised\nI\tdidnt\tknow\tit\twas\tcalled\tthat\tsir\nBut\tI\texpect\tyouve\trealized\tby\tnow\twhat\tit\tdoes\nIt\tit\tshows\tme\tmy\tfamily\nAnd\tit\tshowed\tyour\tfriend\tRon\thimself\tas\tHead\tBoy\nHow\tdid\tyou\tknow\nI\tdont\tneed\ta\tcloak\tto\tbecome\tinvisible\tsaid\tDumbledore\tgently\tNow\ncan\tyou\tthink\twhat\tthe\tMirror\tof\tErised\tshows\tus\tall\nHarry\tshook\this\thead\nLet\tme\texplain\tThe\thappiest\tman\ton\tearth\twould\tbe\table\tto\tuse\tthe\nMirror\tof\tErised\tlike\ta\tnormal\tmirror\tthat\tis\the\twould\tlook\tinto\tit\tand\tsee\nhimself\texactly\tas\the\tis\tDoes\tthat\thelp\nHarry\tthought\tThen\the\tsaid\tslowly\tIt\tshows\tus\twhat\twe\twant\nwhatever\twe\twant\nYes\tand\tno\tsaid\tDumbledore\tquietly\tIt\tshows\tus\tnothing\tmore\tor\tless\nthan\tthe\tdeepest\tmost\tdesperate\tdesire\tof\tour\thearts\tYou\twho\thave\tnever\nknown\tyour\tfamily\tsee\tthem\tstanding\taround\tyou\tRonald\tWeasley\twho\thas\nalways\tbeen\tovershadowed\tby\this\tbrothers\tsees\thimself\tstanding\talone\tthe\nbest\tof\tall\tof\tthem\tHowever\tthis\tmirror\twill\tgive\tus\tneither\tknowledge\tor\ntruth\tMen\thave\twasted\taway\tbefore\tit\tentranced\tby\twhat\tthey\thave\tseen\tor\nbeen\tdriven\tmad\tnot\tknowing\tif\twhat\tit\tshows\tis\treal\tor\teven\tpossible\nThe\tMirror\twill\tbe\tmoved\tto\ta\tnew\thome\ttomorrow\tHarry\tand\tI\task\tyou\nnot\tto\tgo\tlooking\tfor\tit\tagain\tIf\tyou\tever\tdo\trun\tacross\tit\tyou\twill\tnow\tbe\nprepared\nIt\twas\ta\tfew\tseconds\tbefore\the\tnoticed\tanything\tabout\tthe\troom\the\nhad\thidden\tin\nIt\tlooked\tlike\tan\tunused\tclassroom\tThe\tdark\tshapes\tof\tdesks\tand\tchairs\nwere\tpiled\tagainst\tthe\twalls\tand\tthere\twas\tan\tupturned\twastepaper\tbasket\nbut\tpropped\tagainst\tthe\twall\tfacing\thim\twas\tsomething\tthat\tdidnt\tlook\tas\tif\tit\nbelonged\tthere\tsomething\tthat\tlooked\tas\tif\tsomeone\thad\tjust\tput\tit\tthere\tto\nkeep\tit\tout\tof\tthe\tway\nIt\twas\ta\tmagnificent\tmirror\tas\thigh\tas\tthe\tceiling\twith\tan\tornate\tgold\nframe\tstanding\ton\ttwo\tclawed\tfeet\tThere\twas\tan\tinscription\tcarved\taround\nthe\ttop\tErised\tstra\tehru\toyt\tube\tcafru\toyt\ton\twohsi\nHis\tpanic\tfading\tnow\tthat\tthere\twas\tno\tsound\tof\tFilch\tand\tSnape\tHarry\nmoved\tnearer\tto\tthe\tmirror\twanting\tto\tlook\tat\thimself\tbut\tsee\tno\treflection\nagain\tHe\tstepped\tin\tfront\tof\tit\n"]
                ]

In [50]:
reference = ["The narrow path had opened suddenly onto the edge of a great black lake. Perched atop a high mountain on the other side, its windows sparkling in the starry sky, was a vast castle with many turrets and towers.",
                "Text copyright © 1997 by J.K. Rowling.",
                "Professor Snape couldn’t bear being in your father’s debt. . . . I do believe he worked so hard to protect you this year because he felt that would make him and your father even. Then he could go back to hating your father’s memory in peace. ",
                "I think, said Ron, we’re going to have to be chessmen. Well, Harry, you take the place of that bishop, and Hermione, you go there instead of that castle.I’m going to be a knight, said Ron. Ron started to direct the black pieces. They moved silently wherever he sent them. Harry’s knees were trembling. What if they lost? ... I’ve got to be taken. NO! Harry and Hermione shouted. That’s chess! snapped Ron. You’ve got to make some sacrifices! I’ll make my move and she’ll take me—that leaves you free to checkmate the king, Harry! ... He stepped forward, and the white queen pounced. She struck Ron hard across the head with her stone arm, and he crashed to the floor—Hermione screamed but stayed on her square—the white queen dragged Ron to one side. He looked as if he’d been knocked out. Shaking, Harry moved three spaces to the left. The white king took off his crown and threw it at Harry’s feet. They had won. The chessmen parted and bowed, leaving the door ahead clear.",
                "The document does not specify Hermione's life partner, nor does it provide context about how one would know who that partner is. Content not present in the document.",
                "The document does not contain information about future events or what will happen in the next part. Content not present in the document.",
                "He had seen not only himself in the mirror, but a whole crowd of people standing right behind him... Harry was looking at his family, for the first time in his life."
            ]


In [51]:
# To dict
data = {
    "question": questions,
    "answer": answers,
    "contexts": contexts,
    "ground_truths": ground_truths,
    "reference": reference
}

In [40]:
data

{'question': ['Where does Hogwards situated ?',
  'In which year, the book is published?',
  'Why doesn’t Professor Snape like Harry?',
  'What happened in the game of chess ? Who are the players playing ? What is the end result? How ?',
  "Who is Hermione's life partner ? How do you know about that ?",
  'What will happen in the next part ?',
  'What does Harry see in the Mirror of Erised?'],
 'answer': [['Diagon Alley'],
  ['The book is published in 2014.'],
  ["Professor Snape doesn't like Harry because he actually hates him."],
  ["In the game of chess, Harry, Ron, and Hermione played a life-sized game to reach the Sorcerer's Stone. Ron was a knight, Hermione was a castle, and Harry was a bishop. The end result was that Ron sacrificed himself by allowing the opposing queen to take him, which ultimately led to Harry putting the opposing king in checkmate, winning the game. This strategic move allowed them to successfully advance to the next challenge in their quest."],
  ["Ron is He

In [52]:
# Convert dict to dataset
dataset = Dataset.from_dict(data)

In [53]:
dataset

Dataset({
    features: ['question', 'answer', 'contexts', 'ground_truths', 'reference'],
    num_rows: 7
})

In [37]:
from ragas import evaluate

In [38]:
from ragas.metrics import (
    faithfulness,
    answer_relevancy,
    context_recall,
    context_precision,
)

In [54]:
result = evaluate(
    dataset = dataset, 
    metrics=[
        context_precision,
        context_recall,
        faithfulness,
        answer_relevancy,
    ],
)

Evaluating:   0%|          | 0/28 [00:00<?, ?it/s]

No statements were generated from the answer.


In [55]:
result

{'context_precision': 0.4286, 'context_recall': 0.2143, 'faithfulness': 0.4722, 'answer_relevancy': 0.9027}

In [56]:
df = result.to_pandas()

In [57]:
df

user_input  \
0                     Where does Hogwards situated ?   
1              In which year, the book is published?   
2            Why doesn’t Professor Snape like Harry?   
3  What happened in the game of chess ? Who are t...   
4  Who is Hermione's life partner ? How do you kn...   
5                What will happen in the next part ?   
6       What does Harry see in the Mirror of Erised?   

                                  retrieved_contexts  \
0  [They\tsay\the\tmet\tvampires\tin\tthe\tBlack\...   
1  [All\trights\treserved.\tNo\tpart\tof\tthis\tp...   
2  [Harry\tborrowed\tRon’s\tquill\tscribbled\tYes...   
3  [after\tall\tbut\tas\tthey\tonly\thad\todd\tmo...   
4  [\t\nThe\trest\tof\tthe\tteam\thung\tback\tto\...   
5  [Whats\tthe\nmatter\tT\t\nCHAPTER\t\tEIGHT\nTH...   
6  [\tI\tI\tdidnt\tsee\tyou\tsir\nStrange\thow\tn...   

                                            response  \
0                                       Diagon Alley   
1                     The book is published in 2014.   
2  Professor Snape doesn't like Harry because he ...   
3  In the game of chess, Harry, Ron, and Hermione...   
4  Ron is Hermione's life partner. This can be in...   
5  In the next part, Harry will continue to exper...   
6  Harry sees his family standing around him in t...   

                                           reference  context_precision  \
0  The narrow path had opened suddenly onto the e...                0.0   
1             Text copyright © 1997 by J.K. Rowling.                0.0   
2  Professor Snape couldn’t bear being in your fa...                1.0   
3  I think, said Ron, we’re going to have to be c...                1.0   
4  The document does not specify Hermione's life ...                0.0   
5  The document does not contain information abou...                0.0   
6  He had seen not only himself in the mirror, bu...                1.0   

   context_recall  faithfulness  answer_relevancy  
0             0.0           NaN          0.772860  
1             0.0      0.000000          0.952948  
2             0.0      0.500000          0.989664  
3             0.0      0.000000          0.839729  
4             0.5      0.666667          0.956147  
5             1.0      0.666667          0.807650  
6             0.0      1.000000          1.000000